Ca_anal

In [1]:
from IPython import get_ipython
get_ipython().run_line_magic('reset', '-sf') 

In [2]:
import pandas as pd
import glob
from dash import Dash
import dash_core_components as dcc 
import dash_html_components as html 
from dash.dependencies import Input, Output
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import numpy as np
import os
import re
from scipy.signal import savgol_filter
from scipy.signal import find_peaks
import modules.file_folder_handler as file_folder_handler
import modules.data_transformator as data_transformator
import modules.graph_handler as graph_handler
import modules.peak_detector as peak_detector
import modules.data_uploader as data_uploader
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'notebook'

проанализируем трейсы из папки ATP_mtRCaMP_Caff_Ctrl

## Извлекаем данные в датафрейм

In [3]:
%%time
df, type_list, save_directory = file_folder_handler.file_extraction('Fluo_mtRCaMP_check_lambda\Fluo_mtRCamp_lambda_levelCaevent_check\*.csv')
df.reset_index(inplace=True)

CPU times: total: 266 ms
Wall time: 650 ms


In [4]:
file_folder_handler.file_folder_creator(save_directory)

'Folder created'

## Построим графики с SD

Построим графики с +/- 2SD для каждого трейса и сохраним их в виде картинок в соответствующих папках 

In [5]:
filename = df.filename.unique()

разделим наш df по типам dendro/mit/spine

In [6]:
dendro = pd.pivot_table(df, index = 'index', columns = 'filename', values = 'dendro')
dendro ['signal_type'] = 'dendro'
dendro['norm_time'] = np.arange(0, len(dendro)*0.01, 0.01)


mit = pd.pivot_table(df, index = 'index', columns = 'filename', values = 'mit')
mit ['signal_type'] = 'mit'
mit['norm_time'] = np.arange(0, len(mit)*0.01, 0.01)


spine = pd.pivot_table(df, index = 'index', columns = 'filename', values = 'spine')
spine ['signal_type'] = 'spine'
spine['norm_time'] = np.arange(0, len(spine)*0.01, 0.01)


In [7]:
fig = px.line(dendro,x='norm_time', y = dendro.columns[:-2])
fig.show()

In [8]:
fig = px.line(mit,x='norm_time', y = mit.columns[:-2])
fig.show()

In [9]:
#fig = px.line(spine,x='norm_time', y = spine.columns[:-2])
#fig.show()

In [10]:
with pd.ExcelWriter('Fluo_mtRCamp_lambda_levelCaevent_check.xlsx') as writer:
    #for_sd.to_excel(writer, sheet_name='SD', float_format="%.6f")
    dendro.to_excel(writer, sheet_name='dendro', float_format="%.6f")
    mit.to_excel(writer, sheet_name='mit', float_format="%.6f")
    spine.to_excel(writer, sheet_name='spine', float_format="%.6f")